In [31]:
#fundamentals
import matplotlib.pyplot as plt
import seaborn as sns 
import pandas as pd 
import numpy as np
import scipy
import math

#data exploration 
from pandas_profiling import ProfileReport
import cufflinks as cf
cf.go_offline()
cf.set_config_file(offline=True, world_readable=True)
from plotly.offline import iplot

#data preprocessing 
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score, KFold
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler, PowerTransformer, MinMaxScaler
from sklearn.preprocessing import KBinsDiscretizer
from sklearn.compose import ColumnTransformer
from sklearn.decomposition import PCA
from sklearn.impute import SimpleImputer
from imblearn.pipeline import Pipeline
from imblearn.over_sampling import SMOTE
import warnings
from statsmodels.stats.outliers_influence import variance_inflation_factor
import statsmodels.api as sm


#classifiers
from sklearn.linear_model import LinearRegression, SGDRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.svm import LinearSVR, SVR

import xgboost as xgb 
import catboost as cb
import lightgbm as lgb

from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

#metrics for evaluation
from sklearn.metrics import mean_squared_error
from scipy import stats

#saving parameters
from joblib import dump, load

In [32]:
#fixing random seed for repoducability
import random

random.seed(0)
np.random.seed(0)

In [33]:
original_df = pd.read_csv('train.csv')

In [ ]:
profile = ProfileReport(original_df)
profile.to_file(output_file="output.html")
profile

Summarize dataset:   0%|          | 0/30 [00:00<?, ?it/s]

In [ ]:
original_df[original_df['target'] ==0]

In [ ]:
original_df.drop(index = 170514, inplace = True)

In [ ]:
original_df['target'].iplot(kind = 'histogram',filename = 'target_histo.html')

In [ ]:
original_df.drop(labels =['id'], axis = 1, inplace = True)

In [ ]:
train, val = train_test_split(original_df, random_state = 50, train_size = 0.8)

In [ ]:
num_columns = ['cont1','cont2','cont3',
               'cont4','cont5','cont6',
               'cont7','cont8','cont9',
               'cont10','cont11','cont12',
              'cont13','cont14']

In [ ]:
import itertools

def interaction_features(df):
    
    interactions = pd.DataFrame(index=df.index)
    # Iterate through each pair of features, combine them into interaction features
    for col1, col2 in itertools.combinations(num_columns, 2):
        new_col_name = '_'.join([col1, col2])

        # Convert to strings and combine
        interactions[new_col_name] = df[col1] * df[col2]
    return interactions 

In [ ]:
a = interaction_features(train)
b = interaction_features(val)
b.head()

In [ ]:
train_FE = pd.concat([train, a], axis = 1)
train_FE

In [ ]:
new_columns = list(train.columns)

In [ ]:
new_columns.remove('target')
new_columns

In [ ]:
val_FE = pd.concat([val,b],axis=1)

In [ ]:
warnings.filterwarnings('ignore')

num_process = Pipeline([
    ('minmaxscale', StandardScaler())
])

preprocessor = ColumnTransformer([
                                ('num', num_process, new_columns)],
                                remainder = 'passthrough') 

In [ ]:
from sklearn.feature_selection import SelectKBest, f_classif

In [ ]:
X_train = train_FE.drop(labels = 'target', axis = 1)
Y_train = train_FE['target']
X_val = val_FE.drop(labels = 'target', axis = 1)
Y_val = val_FE['target']


# X_train = train.drop(labels = 'target', axis = 1)
# Y_train = train['target']
# X_val = val.drop(labels = 'target', axis = 1)
# Y_val = val['target']

In [16]:
X_train

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
78850   0.707670  0.619905  0.334831  0.628941  0.832495  0.430448  0.412560   
36119   0.327272  0.356516  0.618076  0.303311  0.610909  0.537816  0.576739   
123670  0.467393  0.358361  0.501804  0.851466  0.802002  0.315503  0.377088   
12763   0.520106  0.168235  0.294885  0.275858  0.719473  0.613012  0.420170   
55192   0.948061  0.820781  0.223465  0.475990  0.497556  0.883607  0.638241   
...          ...       ...       ...       ...       ...       ...       ...   
165959  0.669965  0.267008  0.247021  0.498890  0.282104  0.829169  0.752037   
186464  0.474306  0.359148  0.565569  0.315088  0.791018  0.623853  0.542710   
153709  0.721867  0.424421  0.594003  0.730605  0.281399  0.586627  0.811631   
239500  0.439958  0.089989  0.506192  0.797017  0.456215  0.368526  0.373182   
103904  0.245833  0.783075  0.550999  0.837185  0.629644  0.201868  0.295825   

           cont8     cont9    cont10  ...  cont10_cont11  cont10_cont12  \
78850   0.801106  0.587422  0.680544  ...       0.195014       0.341817   
36119   0.358436  0.365183  0.539615  ...       0.264515       0.376360   
123670  0.376216  0.342714  0.438676  ...       0.102791       0.141583   
12763   0.385265  0.597194  0.839359  ...       0.420462       0.534997   
55192   0.803582  0.897365  0.806929  ...       0.637230       0.672211   
...          ...       ...       ...  ...            ...            ...   
165959  0.871217  0.577007  0.819203  ...       0.670018       0.634439   
186464  0.639738  0.377893  0.583425  ...       0.419310       0.268536   
153709  0.908906  0.579120  0.602087  ...       0.447616       0.488435   
239500  0.537294  0.690091  0.412977  ...       0.183959       0.117354   
103904  0.615433  0.293539  0.355216  ...       0.109482       0.089235   

        cont10_cont13  cont10_cont14  cont11_cont12  cont11_cont13  \
78850        0.448128       0.582565       0.143928       0.188693   
36119        0.198965       0.187899       0.341889       0.180742   
123670       0.153091       0.095891       0.075628       0.081775   
12763        0.599399       0.201126       0.319287       0.357723   
55192        0.732381       0.590172       0.657856       0.716742   
...               ...            ...            ...            ...   
165959       0.718016       0.336801       0.633422       0.716864   
186464       0.287850       0.349379       0.330802       0.354594   
153709       0.477979       0.208268       0.603106       0.590195   
239500       0.244778       0.296749       0.126582       0.264024   
103904       0.119467       0.296948       0.077427       0.103659   

        cont11_cont14  cont12_cont13  cont12_cont14  cont13_cont14  
78850        0.245300       0.330737       0.429957       0.563682  
36119        0.170689       0.257165       0.242862       0.128390  
123670       0.051221       0.112635       0.070551       0.076285  
12763        0.120032       0.455168       0.152729       0.171115  
55192        0.577569       0.756087       0.609275       0.663812  
...               ...            ...            ...            ...  
165959       0.336260       0.678798       0.318405       0.360349  
186464       0.430389       0.227091       0.275632       0.295457  
153709       0.257164       0.644016       0.280615       0.274608  
239500       0.320081       0.168431       0.204192       0.425903  
103904       0.257655       0.084488       0.210005       0.281153  

[239999 rows x 105 columns]

In [44]:
LinearRegression().get_params()

{'copy_X': True,
 'fit_intercept': True,
 'n_jobs': None,
 'normalize': False,
 'positive': False}

In [24]:
LinReg = Pipeline(steps = [    
    ('preprocessing', preprocessor),
    ('selectK', SelectKBest(f_classif, k = 60)),
    ('regressor', LinearRegression(n_jobs = -1))])

LinReg_opt = LinReg.fit(X_train,Y_train)

In [102]:
dump(LinReg, 'Tabular_Playground_Jan21_LinReg.joblib')

['Tabular_Playground_Jan21_LinReg.joblib']

In [36]:
LinReg = load('Tabular_Playground_Jan21_LinReg.joblib') 

In [25]:
mean_squared_error(Y_val, LinReg.predict(X_val), squared = False)

0.7224573685538491

In [53]:
mean_squared_error(Y_val, LinReg.predict(X_val), squared = False)

0.719846757349274

In [47]:
DecisionTreeRegressor().get_params()

{'ccp_alpha': 0.0,
 'criterion': 'mse',
 'max_depth': None,
 'max_features': None,
 'max_leaf_nodes': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'random_state': None,
 'splitter': 'best'}

In [15]:
from sklearn.metrics import SCORERS
SCORERS.keys()

dict_keys(['explained_variance', 'r2', 'max_error', 'neg_median_absolute_error', 'neg_mean_absolute_error', 'neg_mean_absolute_percentage_error', 'neg_mean_squared_error', 'neg_mean_squared_log_error', 'neg_root_mean_squared_error', 'neg_mean_poisson_deviance', 'neg_mean_gamma_deviance', 'accuracy', 'top_k_accuracy', 'roc_auc', 'roc_auc_ovr', 'roc_auc_ovo', 'roc_auc_ovr_weighted', 'roc_auc_ovo_weighted', 'balanced_accuracy', 'average_precision', 'neg_log_loss', 'neg_brier_score', 'adjusted_rand_score', 'rand_score', 'homogeneity_score', 'completeness_score', 'v_measure_score', 'mutual_info_score', 'adjusted_mutual_info_score', 'normalized_mutual_info_score', 'fowlkes_mallows_score', 'precision', 'precision_macro', 'precision_micro', 'precision_samples', 'precision_weighted', 'recall', 'recall_macro', 'recall_micro', 'recall_samples', 'recall_weighted', 'f1', 'f1_macro', 'f1_micro', 'f1_samples', 'f1_weighted', 'jaccard', 'jaccard_macro', 'jaccard_micro', 'jaccard_samples', 'jaccard_wei

In [26]:
tree_param_grid = [
    {
    'ccp_alpha': [0.0, 1.0, 2.0], #minimal cost-complexity pruning, used to avoid over fitting 
    'max_depth': [2,16,32,64],
    'min_impurity_decrease': [0.0,2.0,4.0]
    }
]

Dtree_regressor = GridSearchCV(DecisionTreeRegressor(random_state=50), 
                               tree_param_grid, 
                               cv = 3, 
                               return_train_score = True,
                               scoring = 'neg_root_mean_squared_error',
                              n_jobs=-1)
Dtree = Pipeline(steps = [    
    ('preprocessing', preprocessor),
    ('selectK', SelectKBest(f_classif, k = 60)),
    ('tree_regressor', Dtree_regressor)
])

tuned_Dtree = Dtree.fit(X_train, Y_train)

In [27]:
mean_squared_error(Y_val, Dtree.predict(X_val), squared = False)

0.7276933322321317

In [56]:
mean_squared_error(Y_val, Dtree.predict(X_val), squared = False)

0.7276933322321295

In [66]:
mean_squared_error(Y_val, Dtree.predict(X_val), squared = False)

0.7280497290646732

In [103]:
dump(Dtree, 'Tabular_Playground_Jan21_Dtree.joblib')

['Tabular_Playground_Jan21_Dtree.joblib']

In [35]:
Dtree = load('Tabular_Playground_Jan21_Dtree.joblib')

In [21]:
RandomForestRegressor().get_params()

{'bootstrap': True,
 'ccp_alpha': 0.0,
 'criterion': 'mse',
 'max_depth': None,
 'max_features': 'auto',
 'max_leaf_nodes': None,
 'max_samples': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 100,
 'n_jobs': None,
 'oob_score': False,
 'random_state': None,
 'verbose': 0,
 'warm_start': False}

In [59]:
forest_param_grid = [
    {'n_estimators': [8,16,64],
     'max_depth' : [2,4,8]}
]

Rforest_regressor = GridSearchCV(RandomForestRegressor(n_jobs = -1, random_state=50), 
                                 forest_param_grid, 
                                 cv = 3, 
                                 return_train_score = True, 
                                 scoring = 'neg_root_mean_squared_error',
                                 n_jobs=-1)
Rforest = Pipeline(steps = [    
    ('preprocessing', preprocessor),
    ('forest_regressor', Rforest_regressor)
])

tuned_Rforest = Rforest.fit(X_train, Y_train)

In [70]:
mean_squared_error(Y_val, Rforest.predict(X_val), squared = False)

0.7139322662703165

In [60]:
mean_squared_error(Y_val, Rforest.predict(X_val), squared = False)

0.71281306142573

In [104]:
dump(Rforest, 'Tabular_Playground_Jan21_rforest.joblib')

['Tabular_Playground_Jan21_rforest.joblib']

In [34]:
Rforest = load('Tabular_Playground_Jan21_rforest.joblib')

In [19]:
mean_squared_error(Y_val, Rforest.predict(X_val), squared = False)

0.7139322662703165

In [31]:
dropout = [0.1, 0.2, 0.3, 0.4]
units = [256, 512, 1024]
epochs = [50, 100, 200]

def create_model(units = 16, dropout = 0.1):
    model = Sequential()
    model.add(Dense(units=units, activation='relu'))
    model.add(Dropout(dropout))
    model.add(Dense(units=units/2, activation='relu'))
    model.add(Dropout(dropout/2))
    model.add(Dense(units=units/2, activation='relu'))
    model.add(Dropout(dropout/2))
    model.add(Dense(units=units/4, activation='relu'))
    model.add(Dropout(dropout/4))
    model.add(Dense(units=units/8, activation='relu'))
    model.add(Dropout(dropout/8))
    model.add(Dense(units=1, activation = 'linear')) 
    model.compile(optimizer = 'adam', 
                  loss = 'mse')
    return model 

In [32]:
NNregressor = KerasRegressor(build_fn = create_model, batch_size = 2048)

NN_param_grid = dict(dropout = dropout, units= units, epochs = epochs)
NNregressor = GridSearchCV(NNregressor, 
                    param_grid=NN_param_grid, 
                    cv=5, 
                    return_train_score= True,
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)

NN = Pipeline(steps = [ 
    ('preprocessing', preprocessor),
    ('NN_regressor', NNregressor)
])

tuned_NN = NN.fit(X_train, Y_train)

Epoch 1/50
106/106 [==============================] - 2s 5ms/step - loss: 26.1457
Epoch 2/50
106/106 [==============================] - 0s 4ms/step - loss: 1.1835
Epoch 3/50
106/106 [==============================] - 0s 4ms/step - loss: 0.8738
Epoch 4/50
106/106 [==============================] - 0s 4ms/step - loss: 0.8008
Epoch 5/50
106/106 [==============================] - 0s 5ms/step - loss: 0.7553
Epoch 6/50
106/106 [==============================] - 0s 5ms/step - loss: 0.7255
Epoch 7/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7019
Epoch 8/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6886
Epoch 9/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6780
Epoch 10/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6639
Epoch 11/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6560
Epoch 12/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6504
Epoch 13/50
106/106 [===

106/106 [==============================] - 1s 5ms/step - loss: 19.9597
Epoch 2/50
106/106 [==============================] - 0s 4ms/step - loss: 1.1376
Epoch 3/50
106/106 [==============================] - 0s 4ms/step - loss: 0.8796
Epoch 4/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7980
Epoch 5/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7523
Epoch 6/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7225
Epoch 7/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7014
Epoch 8/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6886
Epoch 9/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6759
Epoch 10/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6659
Epoch 11/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6548
Epoch 12/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6503
Epoch 13/50
106/106 [==============

106/106 [==============================] - 1s 4ms/step - loss: 20.7877
Epoch 2/50
106/106 [==============================] - 0s 4ms/step - loss: 1.0947
Epoch 3/50
106/106 [==============================] - 0s 4ms/step - loss: 0.8330
Epoch 4/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7670
Epoch 5/50
106/106 [==============================] - 0s 4ms/step - loss: 0.7242
Epoch 6/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6978
Epoch 7/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6798
Epoch 8/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6721
Epoch 9/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6515
Epoch 10/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6451
Epoch 11/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6351
Epoch 12/50
106/106 [==============================] - 0s 4ms/step - loss: 0.6292
Epoch 13/50
106/106 [==============

106/106 [==============================] - 1s 5ms/step - loss: 16.1496
Epoch 2/50
106/106 [==============================] - 1s 5ms/step - loss: 0.8608
Epoch 3/50
106/106 [==============================] - 1s 5ms/step - loss: 0.7449
Epoch 4/50
106/106 [==============================] - 1s 5ms/step - loss: 0.7126
Epoch 5/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6920
Epoch 6/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6742
Epoch 7/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6630
Epoch 8/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6491
Epoch 9/50
106/106 [==============================] - 0s 5ms/step - loss: 0.6484
Epoch 10/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6353
Epoch 11/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6248
Epoch 12/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6152
Epoch 13/50
106/106 [==============

106/106 [==============================] - 1s 5ms/step - loss: 16.3742
Epoch 2/50
106/106 [==============================] - 1s 5ms/step - loss: 0.8647
Epoch 3/50
106/106 [==============================] - 1s 5ms/step - loss: 0.7291
Epoch 4/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6934
Epoch 5/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6651
Epoch 6/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6556
Epoch 7/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6397
Epoch 8/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6355
Epoch 9/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6249
Epoch 10/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6178
Epoch 11/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6066
Epoch 12/50
106/106 [==============================] - 1s 5ms/step - loss: 0.6078
Epoch 13/50
106/106 [==============

...

106/106 [==============================] - 1s 6ms/step - loss: 0.5010
Epoch 188/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4989
Epoch 189/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4999
Epoch 190/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4972
Epoch 191/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4983
Epoch 192/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4977
Epoch 193/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4968
Epoch 194/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4987
Epoch 195/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4971
Epoch 196/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4946
Epoch 197/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4950
Epoch 198/200
106/106 [==============================] - 1s 7ms/step - loss: 0.4938
Epoch 

106/106 [==============================] - 1s 6ms/step - loss: 0.5044
Epoch 183/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5009
Epoch 184/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5004
Epoch 185/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5005
Epoch 186/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4988
Epoch 187/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5015
Epoch 188/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4992
Epoch 189/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4995
Epoch 190/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4992
Epoch 191/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4999
Epoch 192/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4984
Epoch 193/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4977
Epoch 

106/106 [==============================] - 1s 6ms/step - loss: 0.5065
Epoch 178/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5062
Epoch 179/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5041
Epoch 180/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5063
Epoch 181/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5036
Epoch 182/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5028
Epoch 183/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5076
Epoch 184/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5029
Epoch 185/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5026
Epoch 186/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4986
Epoch 187/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5018
Epoch 188/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5010
Epoch 

Epoch 173/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5045
Epoch 174/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5054
Epoch 175/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5063
Epoch 176/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5023
Epoch 177/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5035
Epoch 178/200
106/106 [==============================] - 1s 6ms/step - loss: 0.5068
Epoch 179/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5010
Epoch 180/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5041
Epoch 181/200
106/106 [==============================] - 1s 6ms/step - loss: 0.4987
Epoch 182/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5002
Epoch 183/200
106/106 [==============================] - 1s 7ms/step - loss: 0.5017
Epoch 184/200
106/106 [==============================] - 1s 6ms/step - loss:

118/118 [==============================] - 1s 4ms/step - loss: 0.5136
Epoch 170/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5151
Epoch 171/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5129
Epoch 172/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5139
Epoch 173/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5151
Epoch 174/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5121
Epoch 175/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5139
Epoch 176/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5124
Epoch 177/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5154
Epoch 178/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5144
Epoch 179/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5140
Epoch 180/200
118/118 [==============================] - 1s 4ms/step - loss: 0.5141
Epoch 

In [33]:
mean_squared_error(Y_val, NN.predict(X_val), squared = False)

0.7088794001883538

In [72]:
NN[1].best_estimator_.model.save('keras_saved_model.pkl')

INFO:tensorflow:Assets written to: keras_saved_model.pkl\assets


In [35]:
import kerastuner as kt

In [38]:
xgb.XGBRegressor().get_params()

{'objective': 'reg:squarederror',
 'base_score': None,
 'booster': None,
 'colsample_bylevel': None,
 'colsample_bynode': None,
 'colsample_bytree': None,
 'gamma': None,
 'gpu_id': None,
 'importance_type': 'gain',
 'interaction_constraints': None,
 'learning_rate': None,
 'max_delta_step': None,
 'max_depth': None,
 'min_child_weight': None,
 'missing': nan,
 'monotone_constraints': None,
 'n_estimators': 100,
 'n_jobs': None,
 'num_parallel_tree': None,
 'random_state': None,
 'reg_alpha': None,
 'reg_lambda': None,
 'scale_pos_weight': None,
 'subsample': None,
 'tree_method': None,
 'validate_parameters': None,
 'verbosity': None}

In [63]:
xgb_params_grid ={'max_depth': [2,4,8,16,24,30]}

model_xgb = xgb.XGBRegressor(n_estimators= 500, 
                             n_jobs = -1, 
                             random_state = 50,
                             gpu_id = 0, 
                             tuned_xgbree_method='gpu_hist')

xgboostregressor = GridSearchCV(model_xgb, 
                    param_grid=xgb_params_grid, 
                    cv=3, 
                    return_train_score= True, 
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)

xgb_pipe = Pipeline(steps = [ 
    ('preprocessing', preprocessor),
    ('xgb_regressor', xgboostregressor)
])

tuned_xgb = xgb_pipe.fit(X_train, Y_train)

[01:31:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:541: 
Parameters: { tuned_xgbree_method } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.




In [42]:
mean_squared_error(Y_val, xgb_pipe.predict(X_val), squared = False)

0.7029499612341704

In [105]:
dump(xgb_pipe, 'Tabular_Playground_Jan21_xgb.joblib')

['Tabular_Playground_Jan21_xgb.joblib']

In [33]:
xgb_pipe = load('Tabular_Playground_Jan21_xgb.joblib')

In [67]:
mean_squared_error(Y_val, xgb_pipe.predict(X_val), squared = False)

0.7032313505871222

In [45]:
LinearSVR().get_params()

{'C': 1.0,
 'dual': True,
 'epsilon': 0.0,
 'fit_intercept': True,
 'intercept_scaling': 1.0,
 'loss': 'epsilon_insensitive',
 'max_iter': 1000,
 'random_state': None,
 'tol': 0.0001,
 'verbose': 0}

In [64]:
svr_params_grid = {'C': [0.01, 1, 100, 1000, 1e5], 
     'tol': [0.01, 1, 100, 1000, 1e5]}
  
model_svr = LinearSVR(verbose =1)

svr_grid = GridSearchCV(model_svr, 
                    param_grid=svr_params_grid, 
                    cv=3, 
                    return_train_score= True, 
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)

svr_pipe = Pipeline(steps = [ 
    ('preprocessing', preprocessor),
    ('svr', svr_grid)
])

tuned_svr = svr_pipe.fit(X_train, Y_train)

[LibLinear]

In [106]:
dump(svr_pipe, 'Tabular_Playground_Jan21_svr.joblib')

['Tabular_Playground_Jan21_svr.joblib']

In [68]:
mean_squared_error(Y_val, svr_pipe.predict(X_val), squared = False)

0.7250544797002983

In [32]:
svr_pipe = load('Tabular_Playground_Jan21_svr.joblib')

In [23]:
mean_squared_error(Y_val, svr_pipe.predict(X_val), squared = False)

0.7316962532443716

In [56]:
lgb.LGBMRegressor().get_params()

{'boosting_type': 'gbdt',
 'class_weight': None,
 'colsample_bytree': 1.0,
 'importance_type': 'split',
 'learning_rate': 0.1,
 'max_depth': -1,
 'min_child_samples': 20,
 'min_child_weight': 0.001,
 'min_split_gain': 0.0,
 'n_estimators': 100,
 'n_jobs': -1,
 'num_leaves': 31,
 'objective': None,
 'random_state': None,
 'reg_alpha': 0.0,
 'reg_lambda': 0.0,
 'silent': True,
 'subsample': 1.0,
 'subsample_for_bin': 200000,
 'subsample_freq': 0}

In [28]:
params={'random_state': 33,
 'min_data_per_group': 5,
 'boosting_type': 'gbdt',
 'num_leaves': 256,
 'max_depth': -1,
 'learning_rate': 0.02,
 'subsample_for_bin': 200000,
 'lambda_l1': 1.074622455507616e-05,
 'lambda_l2': 2.0521330798729704e-06,
 'n_jobs': -1,
 'cat_smooth': 1.0,
 'silent': True,
 'importance_type': 'split',
 'metric': 'rmse',
 'feature_pre_filter': False,
 'bagging_fraction': 0.8206341150202605,
 'min_data_in_leaf': 100,
 'min_sum_hessian_in_leaf': 0.001,
 'bagging_freq': 6,
 'feature_fraction': 0.5,
 'min_gain_to_split': 0.0,
 'min_child_samples': 20}

In [29]:
kaggle_lgb = lgb.LGBMRegressor(**params)

kaggle_lgb.fit(X_train, Y_train)

[LightGBM] [Warning] feature_fraction is set=0.5, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_gain_to_split is set=0.0, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0
[LightGBM] [Warning] lambda_l1 is set=1.074622455507616e-05, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.074622455507616e-05
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.001, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.001
[LightGBM] [Warning] bagging_fraction is set=0.8206341150202605, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8206341150202605
[LightGBM] [Warning] lambda_l2 is set=2.0521330798729704e-06, reg_lambda=0.0 will be ignored. Current value: lambda_l2=2.0521330798729704e-06
[LightGBM] [Warning] bagging_freq is set=6, subsample_fr

LGBMRegressor(bagging_fraction=0.8206341150202605, bagging_freq=6,
              cat_smooth=1.0, feature_fraction=0.5, feature_pre_filter=False,
              lambda_l1=1.074622455507616e-05, lambda_l2=2.0521330798729704e-06,
              learning_rate=0.02, metric='rmse', min_data_in_leaf=100,
              min_data_per_group=5, min_gain_to_split=0.0,
              min_sum_hessian_in_leaf=0.001, num_leaves=256, random_state=33)

In [30]:
mean_squared_error(Y_val, kaggle_lgb.predict(X_val), squared = False)

0.7065216114585431

In [65]:
lgb_params_grid ={'max_depth': [2,4,8,16,24,-1],
                 'num_leaves': [10,31,50],
                 'reg_alpha':[0, 0.1, 1]}

model_lgb = lgb.LGBMRegressor(n_estimators = 200, n_jobs = -1)

lgbregressor = GridSearchCV(model_lgb, 
                    param_grid=lgb_params_grid, 
                    cv=3, 
                    return_train_score= True, 
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)

lgb_pipe = Pipeline(steps = [ 
    ('preprocessing', preprocessor),
    ('lgb_regressor', lgbregressor)
])

tuned_lgb = lgb_pipe.fit(X_train, Y_train)

In [107]:
dump(lgb_pipe, 'Tabular_Playground_Jan21_lgb.joblib')

['Tabular_Playground_Jan21_lgb.joblib']

In [31]:
lgb_pipe = load('Tabular_Playground_Jan21_lgb.joblib')

In [69]:
mean_squared_error(Y_val, lgb_pipe.predict(X_val), squared = False)

0.6996750667908358

In [59]:
mean_squared_error(Y_val, lgb_pipe.predict(X_val), squared = False)

0.699191227250108

In [60]:
cb.CatBoostRegressor().get_params()

{'loss_function': 'RMSE'}

In [66]:
cb_params_grid ={}

model_cb = cb.CatBoostRegressor()

cbregressor = GridSearchCV(model_cb, 
                    param_grid=cb_params_grid, 
                    cv=3, 
                    return_train_score= True, 
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)

cb_pipe = Pipeline(steps = [ 
    ('preprocessing', preprocessor),
    ('cb_regressor', cbregressor)
])

tuned_cb = cb_pipe.fit(X_train, Y_train)

Learning rate set to 0.103533
0:	learn: 0.7311334	total: 96.6ms	remaining: 1m 36s
1:	learn: 0.7293374	total: 140ms	remaining: 1m 9s
2:	learn: 0.7279168	total: 184ms	remaining: 1m 1s
3:	learn: 0.7267281	total: 231ms	remaining: 57.6s
4:	learn: 0.7256093	total: 275ms	remaining: 54.7s
5:	learn: 0.7246397	total: 314ms	remaining: 52s
6:	learn: 0.7238537	total: 355ms	remaining: 50.3s
7:	learn: 0.7230111	total: 401ms	remaining: 49.7s
8:	learn: 0.7222360	total: 444ms	remaining: 48.8s
9:	learn: 0.7215332	total: 485ms	remaining: 48s
10:	learn: 0.7210382	total: 521ms	remaining: 46.8s
11:	learn: 0.7203899	total: 565ms	remaining: 46.5s
12:	learn: 0.7198856	total: 604ms	remaining: 45.9s
13:	learn: 0.7193458	total: 649ms	remaining: 45.7s
14:	learn: 0.7189411	total: 691ms	remaining: 45.4s
15:	learn: 0.7185635	total: 729ms	remaining: 44.8s
16:	learn: 0.7181833	total: 766ms	remaining: 44.3s
17:	learn: 0.7178265	total: 807ms	remaining: 44s
18:	learn: 0.7174945	total: 843ms	remaining: 43.5s
19:	learn: 0.71

160:	learn: 0.7024480	total: 6.51s	remaining: 33.9s
161:	learn: 0.7024039	total: 6.54s	remaining: 33.8s
162:	learn: 0.7023374	total: 6.58s	remaining: 33.8s
163:	learn: 0.7022570	total: 6.62s	remaining: 33.7s
164:	learn: 0.7021762	total: 6.66s	remaining: 33.7s
165:	learn: 0.7021321	total: 6.69s	remaining: 33.6s
166:	learn: 0.7020742	total: 6.73s	remaining: 33.6s
167:	learn: 0.7019860	total: 6.77s	remaining: 33.5s
168:	learn: 0.7019091	total: 6.8s	remaining: 33.4s
169:	learn: 0.7018502	total: 6.83s	remaining: 33.4s
170:	learn: 0.7017616	total: 6.87s	remaining: 33.3s
171:	learn: 0.7016894	total: 6.91s	remaining: 33.3s
172:	learn: 0.7016320	total: 6.95s	remaining: 33.2s
173:	learn: 0.7015749	total: 6.98s	remaining: 33.1s
174:	learn: 0.7015313	total: 7.02s	remaining: 33.1s
175:	learn: 0.7014639	total: 7.06s	remaining: 33s
176:	learn: 0.7013886	total: 7.1s	remaining: 33s
177:	learn: 0.7013390	total: 7.13s	remaining: 33s
178:	learn: 0.7012887	total: 7.17s	remaining: 32.9s
179:	learn: 0.701220

320:	learn: 0.6938523	total: 12.6s	remaining: 26.7s
321:	learn: 0.6938093	total: 12.6s	remaining: 26.6s
322:	learn: 0.6937702	total: 12.7s	remaining: 26.6s
323:	learn: 0.6937200	total: 12.7s	remaining: 26.5s
324:	learn: 0.6936715	total: 12.7s	remaining: 26.5s
325:	learn: 0.6936265	total: 12.8s	remaining: 26.4s
326:	learn: 0.6935737	total: 12.8s	remaining: 26.4s
327:	learn: 0.6935295	total: 12.8s	remaining: 26.3s
328:	learn: 0.6934847	total: 12.9s	remaining: 26.3s
329:	learn: 0.6934451	total: 12.9s	remaining: 26.2s
330:	learn: 0.6933987	total: 13s	remaining: 26.2s
331:	learn: 0.6933481	total: 13s	remaining: 26.1s
332:	learn: 0.6933027	total: 13s	remaining: 26.1s
333:	learn: 0.6932630	total: 13.1s	remaining: 26s
334:	learn: 0.6932183	total: 13.1s	remaining: 26s
335:	learn: 0.6931684	total: 13.1s	remaining: 26s
336:	learn: 0.6931387	total: 13.2s	remaining: 25.9s
337:	learn: 0.6931016	total: 13.2s	remaining: 25.9s
338:	learn: 0.6930618	total: 13.3s	remaining: 25.8s
339:	learn: 0.6930137	to

484:	learn: 0.6872024	total: 18.8s	remaining: 19.9s
485:	learn: 0.6871634	total: 18.8s	remaining: 19.9s
486:	learn: 0.6871288	total: 18.9s	remaining: 19.9s
487:	learn: 0.6870686	total: 18.9s	remaining: 19.8s
488:	learn: 0.6870301	total: 18.9s	remaining: 19.8s
489:	learn: 0.6869956	total: 19s	remaining: 19.7s
490:	learn: 0.6869601	total: 19s	remaining: 19.7s
491:	learn: 0.6869344	total: 19s	remaining: 19.7s
492:	learn: 0.6868971	total: 19.1s	remaining: 19.6s
493:	learn: 0.6868692	total: 19.1s	remaining: 19.6s
494:	learn: 0.6868432	total: 19.1s	remaining: 19.5s
495:	learn: 0.6867976	total: 19.2s	remaining: 19.5s
496:	learn: 0.6867608	total: 19.2s	remaining: 19.5s
497:	learn: 0.6867211	total: 19.3s	remaining: 19.4s
498:	learn: 0.6866898	total: 19.3s	remaining: 19.4s
499:	learn: 0.6866444	total: 19.3s	remaining: 19.3s
500:	learn: 0.6866109	total: 19.4s	remaining: 19.3s
501:	learn: 0.6865687	total: 19.4s	remaining: 19.3s
502:	learn: 0.6865433	total: 19.4s	remaining: 19.2s
503:	learn: 0.6865

648:	learn: 0.6813418	total: 25s	remaining: 13.5s
649:	learn: 0.6813040	total: 25s	remaining: 13.5s
650:	learn: 0.6812763	total: 25.1s	remaining: 13.4s
651:	learn: 0.6812389	total: 25.1s	remaining: 13.4s
652:	learn: 0.6812103	total: 25.2s	remaining: 13.4s
653:	learn: 0.6811754	total: 25.2s	remaining: 13.3s
654:	learn: 0.6811439	total: 25.2s	remaining: 13.3s
655:	learn: 0.6811083	total: 25.3s	remaining: 13.3s
656:	learn: 0.6810808	total: 25.3s	remaining: 13.2s
657:	learn: 0.6810589	total: 25.3s	remaining: 13.2s
658:	learn: 0.6810188	total: 25.4s	remaining: 13.1s
659:	learn: 0.6809778	total: 25.4s	remaining: 13.1s
660:	learn: 0.6809437	total: 25.5s	remaining: 13.1s
661:	learn: 0.6809051	total: 25.5s	remaining: 13s
662:	learn: 0.6808790	total: 25.5s	remaining: 13s
663:	learn: 0.6808405	total: 25.6s	remaining: 12.9s
664:	learn: 0.6808087	total: 25.6s	remaining: 12.9s
665:	learn: 0.6807736	total: 25.7s	remaining: 12.9s
666:	learn: 0.6807474	total: 25.7s	remaining: 12.8s
667:	learn: 0.680702

811:	learn: 0.6760494	total: 31.3s	remaining: 7.24s
812:	learn: 0.6760252	total: 31.3s	remaining: 7.2s
813:	learn: 0.6759926	total: 31.3s	remaining: 7.16s
814:	learn: 0.6759552	total: 31.4s	remaining: 7.12s
815:	learn: 0.6759277	total: 31.4s	remaining: 7.08s
816:	learn: 0.6758962	total: 31.5s	remaining: 7.05s
817:	learn: 0.6758693	total: 31.5s	remaining: 7.01s
818:	learn: 0.6758332	total: 31.5s	remaining: 6.97s
819:	learn: 0.6758064	total: 31.6s	remaining: 6.93s
820:	learn: 0.6757705	total: 31.6s	remaining: 6.89s
821:	learn: 0.6757444	total: 31.7s	remaining: 6.85s
822:	learn: 0.6757162	total: 31.7s	remaining: 6.82s
823:	learn: 0.6756800	total: 31.7s	remaining: 6.78s
824:	learn: 0.6756450	total: 31.8s	remaining: 6.74s
825:	learn: 0.6756098	total: 31.8s	remaining: 6.7s
826:	learn: 0.6755848	total: 31.8s	remaining: 6.66s
827:	learn: 0.6755517	total: 31.9s	remaining: 6.62s
828:	learn: 0.6755079	total: 31.9s	remaining: 6.58s
829:	learn: 0.6754837	total: 32s	remaining: 6.55s
830:	learn: 0.67

972:	learn: 0.6713613	total: 37.4s	remaining: 1.04s
973:	learn: 0.6713354	total: 37.4s	remaining: 998ms
974:	learn: 0.6713106	total: 37.4s	remaining: 960ms
975:	learn: 0.6712812	total: 37.5s	remaining: 921ms
976:	learn: 0.6712453	total: 37.5s	remaining: 883ms
977:	learn: 0.6712201	total: 37.5s	remaining: 845ms
978:	learn: 0.6711920	total: 37.6s	remaining: 806ms
979:	learn: 0.6711592	total: 37.6s	remaining: 768ms
980:	learn: 0.6711313	total: 37.7s	remaining: 730ms
981:	learn: 0.6710954	total: 37.7s	remaining: 691ms
982:	learn: 0.6710610	total: 37.7s	remaining: 653ms
983:	learn: 0.6710389	total: 37.8s	remaining: 614ms
984:	learn: 0.6710059	total: 37.8s	remaining: 576ms
985:	learn: 0.6709720	total: 37.9s	remaining: 538ms
986:	learn: 0.6709414	total: 37.9s	remaining: 499ms
987:	learn: 0.6709092	total: 37.9s	remaining: 461ms
988:	learn: 0.6708865	total: 38s	remaining: 422ms
989:	learn: 0.6708592	total: 38s	remaining: 384ms
990:	learn: 0.6708327	total: 38.1s	remaining: 346ms
991:	learn: 0.67

In [108]:
dump(cb_pipe, 'Tabular_Playground_Jan21_cb.joblib')

['Tabular_Playground_Jan21_cb.joblib']

In [64]:
mean_squared_error(Y_val, cb_pipe.predict(X_val), squared = False)

0.6982101824546937

In [30]:
cb_pipe = load('Tabular_Playground_Jan21_cb.joblib')

In [70]:
mean_squared_error(Y_val, cb_pipe.predict(X_val), squared = False)

0.6990879097474328

In [87]:
test = pd.read_csv('test.csv', index_col = 'id')

In [88]:
test.head()

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
id                                                                         
0   0.353600  0.738780  0.600939  0.293377  0.285691  0.458006  0.620704   
2   0.907222  0.189756  0.215531  0.869915  0.301333  0.528958  0.390351   
6   0.179287  0.355353  0.623972  0.437812  0.282476  0.320826  0.386789   
7   0.359385  0.181049  0.551368  0.206386  0.280763  0.482076  0.506677   
10  0.335791  0.682607  0.676481  0.219465  0.282861  0.581721  0.748639   

       cont8     cont9    cont10    cont11    cont12    cont13    cont14  
id                                                                        
0   0.422249  0.369203  0.435727  0.550540  0.699134  0.286864  0.364515  
2   0.521112  0.794779  0.798580  0.446475  0.449037  0.916964  0.513002  
6   0.776422  0.222268  0.229102  0.211913  0.222651  0.327164  0.827941  
7   0.362793  0.379737  0.345686  0.445276  0.518485  0.299028  0.598166  
10  0.350158  0.448915  0.506878  0.817721  0.805895  0.790591  0.249275

In [62]:
test.drop(columns=['id'], inplace=True)

In [86]:
submission2 = pd.read_csv('sample_submission.csv', index_col='id')

In [89]:
test

c = interaction_features(test)

test_FE = pd.concat([test, c], axis = 1)
test_FE

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
id                                                                             
0       0.353600  0.738780  0.600939  0.293377  0.285691  0.458006  0.620704   
2       0.907222  0.189756  0.215531  0.869915  0.301333  0.528958  0.390351   
6       0.179287  0.355353  0.623972  0.437812  0.282476  0.320826  0.386789   
7       0.359385  0.181049  0.551368  0.206386  0.280763  0.482076  0.506677   
10      0.335791  0.682607  0.676481  0.219465  0.282861  0.581721  0.748639   
...          ...       ...       ...       ...       ...       ...       ...   
499984  0.353856  0.677578  0.550852  0.869612  0.957635  0.255054  0.289138   
499985  0.243209  0.135627  0.218393  0.792798  0.547639  0.433520  0.549540   
499987  0.506973  0.683893  0.533434  0.192957  0.314381  0.358604  0.554455   
499988  0.347870  0.553112  0.495284  0.861500  0.816914  0.298478  0.275964   
499990  0.688188  0.358328  0.644511  0.766354  0.747591  0.727329  0.468329   

           cont8     cont9    cont10  ...  cont10_cont11  cont10_cont12  \
id                                    ...                                 
0       0.422249  0.369203  0.435727  ...       0.239885       0.304632   
2       0.521112  0.794779  0.798580  ...       0.356546       0.358592   
6       0.776422  0.222268  0.229102  ...       0.048550       0.051010   
7       0.362793  0.379737  0.345686  ...       0.153926       0.179233   
10      0.350158  0.448915  0.506878  ...       0.414485       0.408491   
...          ...       ...       ...  ...            ...            ...   
499984  0.635979  0.271399  0.282455  ...       0.061340       0.061882   
499985  0.650107  0.453787  0.459689  ...       0.207055       0.234982   
499987  0.267105  0.396101  0.445390  ...       0.170431       0.177256   
499988  0.265841  0.334250  0.252635  ...       0.053960       0.072057   
499990  0.576711  0.453124  0.381600  ...       0.114147       0.190658   

        cont10_cont13  cont10_cont14  cont11_cont12  cont11_cont13  \
id                                                                   
0            0.124994       0.158829       0.384901       0.157930   
2            0.732269       0.409673       0.200484       0.409401   
6            0.074954       0.189683       0.047183       0.069330   
7            0.103370       0.206778       0.230869       0.133150   
10           0.400733       0.126352       0.658998       0.646483   
...               ...            ...            ...            ...   
499984       0.105429       0.076963       0.047579       0.081061   
499985       0.146334       0.181920       0.230246       0.143385   
499987       0.169798       0.164556       0.152289       0.145882   
499988       0.085080       0.098150       0.060921       0.071931   
499990       0.263716       0.254951       0.149451       0.206719   

        cont11_cont14  cont12_cont13  cont12_cont14  cont13_cont14  
id                                                                  
0            0.200680       0.200556       0.254845       0.104566  
2            0.229043       0.411751       0.230357       0.470405  
6            0.175451       0.072843       0.184342       0.270872  
7            0.266349       0.155041       0.310140       0.178868  
10           0.203838       0.637134       0.200890       0.197075  
...               ...            ...            ...            ...  
499984       0.059174       0.081777       0.059697       0.101706  
499985       0.178254       0.162725       0.202296       0.125980  
499987       0.141378       0.151723       0.147039       0.140853  
499988       0.082980       0.096055       0.110811       0.130837  
499990       0.199849       0.345281       0.333805       0.461715  

[200000 rows x 105 columns]

In [98]:
test.index

Int64Index([     0,      2,      6,      7,     10,     14,     16,     17,
                18,     19,
            ...
            499973, 499977, 499979, 499982, 499983, 499984, 499985, 499987,
            499988, 499990],
           dtype='int64', name='id', length=200000)

In [102]:
workings = pd.DataFrame(index = test.index)
workings

Empty DataFrame
Columns: []
Index: [0, 2, 6, 7, 10, 14, 16, 17, 18, 19, 21, 28, 29, 30, 31, 34, 35, 36, 38, 40, 41, 42, 43, 44, 46, 47, 48, 50, 53, 54, 61, 63, 65, 67, 74, 79, 81, 84, 87, 88, 89, 90, 93, 94, 96, 97, 101, 105, 106, 110, 111, 112, 115, 116, 117, 125, 127, 128, 129, 132, 133, 134, 136, 138, 141, 142, 143, 144, 147, 148, 155, 157, 163, 164, 166, 168, 172, 174, 176, 179, 180, 188, 199, 201, 203, 206, 209, 211, 214, 217, 222, 223, 230, 231, 234, 236, 238, 246, 247, 248, ...]

[200000 rows x 0 columns]

In [103]:
workings['cb'] = cb_pipe.predict(test_FE)
workings['xgb'] = xgb_pipe.predict(test_FE)
workings['lgb'] = lgb_pipe.predict(test_FE)
workings.tail()

cb       xgb       lgb
id                                  
499984  8.153291  8.141283  8.168666
499985  8.158687  8.181958  8.134179
499987  8.178734  8.154364  8.181750
499988  8.058155  8.088582  8.034272
499990  7.962177  8.078520  8.057529

In [104]:
submission2['target'] = workings.mean(axis=1)
submission2['target'].tail()

id
499984    8.154413
499985    8.158275
499987    8.171616
499988    8.060336
499990    8.032742
Name: target, dtype: float64

In [105]:
submission2['target']

id
0         7.953476
2         7.835884
6         7.933788
7         8.182387
10        8.225323
            ...   
499984    8.154413
499985    8.158275
499987    8.171616
499988    8.060336
499990    8.032742
Name: target, Length: 200000, dtype: float64

In [107]:
submission2.to_csv('submission_results2.csv')

id
0         7.953476
2         7.933788
6         8.200757
7         7.768312
10        7.645461
            ...   
499984         NaN
499985         NaN
499987         NaN
499988         NaN
499990         NaN
Name: target, Length: 200000, dtype: float64

In [33]:
SVR().get_params()

{'C': 1.0,
 'cache_size': 200,
 'coef0': 0.0,
 'degree': 3,
 'epsilon': 0.1,
 'gamma': 'scale',
 'kernel': 'rbf',
 'max_iter': -1,
 'shrinking': True,
 'tol': 0.001,
 'verbose': False}

In [34]:
StackingRegressor(regressors = [LinReg, 
             Dtree, 
             Rforest, 
             xgb_pipe,
             svr_pipe,
             lgb_pipe,
             cb_pipe],
            meta_regressor = LinearSVR()).get_params()

{'meta_regressor__C': 1.0,
 'meta_regressor__dual': True,
 'meta_regressor__epsilon': 0.0,
 'meta_regressor__fit_intercept': True,
 'meta_regressor__intercept_scaling': 1.0,
 'meta_regressor__loss': 'epsilon_insensitive',
 'meta_regressor__max_iter': 1000,
 'meta_regressor__random_state': None,
 'meta_regressor__tol': 0.0001,
 'meta_regressor__verbose': 0,
 'meta_regressor': LinearSVR(),
 'refit': True,
 'regressors': [Pipeline(steps=[('preprocessing',
                   ColumnTransformer(remainder='passthrough',
                                     transformers=[('num',
                                                    Pipeline(steps=[('minmaxscale',
                                                                     MinMaxScaler())]),
                                                    ['cont1', 'cont2', 'cont3',
                                                     'cont4', 'cont5', 'cont6',
                                                     'cont7', 'cont8', 'cont9',
          

In [72]:
from sklearn.ensemble import StackingRegressor 

In [101]:
regressors = [('Linear Regression', LinReg),
          ('Decision Tree', Dtree),
          ('Random Forest', Rforest),
          ('XGB Regressor', xgb_pipe),
           ('svr',    svr_pipe),
          ('LightGB Regressor', lgb_pipe),
          ('CatBoost Regressor', cb_pipe)]


stacker_model = StackingRegressor(estimators = regressors, 
                        final_estimator = cb.CatBoostRegressor(),
                        n_jobs = -1,
                        verbose = 1)

labels = ['Linear Regression', 
          'Decision Tree', 
          'Random Forest', 
          'XGB Regressor',
          'LightGB Regressor',
          'CatBoost Regressor',
          'Stacking']
                                    

stacker_model.fit(X_train, Y_train)

ValueError: Input contains NaN, infinity or a value too large for dtype('float64').

In [47]:
regressors = [
          xgb_pipe,
          lgb_pipe,
          cb_pipe]

predictions = pd.DataFrame()
prediction = pd.Series
for reg in regressors:
    prediction = pd.Series(reg.predict(X_val))
    predictions[regressors.index(reg)] = prediction
        
predictions.head()

0         1         2
0  8.021277  8.118279  8.170052
1  7.850214  7.830854  7.810715
2  7.690536  7.710285  7.795841
3  8.071290  8.061442  8.056379
4  8.022994  7.985992  8.021769

In [48]:
predictions['avg_predictions'] = predictions.mean(axis=1)

In [49]:
predictions

0         1         2  avg_predictions
0      8.021277  8.118279  8.170052         8.103203
1      7.850214  7.830854  7.810715         7.830594
2      7.690536  7.710285  7.795841         7.732221
3      8.071290  8.061442  8.056379         8.063037
4      8.022994  7.985992  8.021769         8.010252
...         ...       ...       ...              ...
59995  7.908706  8.074931  7.968637         7.984091
59996  7.783975  7.833416  7.704733         7.774041
59997  7.778489  7.895082  7.833295         7.835622
59998  7.893311  7.806200  7.830522         7.843344
59999  7.990673  7.994854  8.015310         8.000279

[60000 rows x 4 columns]

In [50]:
mean_squared_error(Y_val, predictions['avg_predictions'], squared = False)

0.6990872106685811

In [76]:
stacker_cb_model = cb.CatBoostRegressor()

stacker_cb_model.fit(predictions, Y_train)

Learning rate set to 0.103533
0:	learn: 0.7208673	total: 18.1ms	remaining: 18.1s
1:	learn: 0.7107667	total: 36.4ms	remaining: 18.1s
2:	learn: 0.7021342	total: 52.1ms	remaining: 17.3s
3:	learn: 0.6950586	total: 68.4ms	remaining: 17s
4:	learn: 0.6891873	total: 85.3ms	remaining: 17s
5:	learn: 0.6840322	total: 102ms	remaining: 16.8s
6:	learn: 0.6797316	total: 120ms	remaining: 17s
7:	learn: 0.6761502	total: 138ms	remaining: 17.1s
8:	learn: 0.6729653	total: 157ms	remaining: 17.3s
9:	learn: 0.6704951	total: 175ms	remaining: 17.3s
10:	learn: 0.6682051	total: 192ms	remaining: 17.3s
11:	learn: 0.6661437	total: 210ms	remaining: 17.3s
12:	learn: 0.6643935	total: 227ms	remaining: 17.2s
13:	learn: 0.6629003	total: 244ms	remaining: 17.2s
14:	learn: 0.6616450	total: 261ms	remaining: 17.2s
15:	learn: 0.6604311	total: 279ms	remaining: 17.2s
16:	learn: 0.6593331	total: 297ms	remaining: 17.2s
17:	learn: 0.6583113	total: 315ms	remaining: 17.2s
18:	learn: 0.6574822	total: 334ms	remaining: 17.2s
19:	learn: 0

166:	learn: 0.6416362	total: 2.93s	remaining: 14.6s
167:	learn: 0.6416039	total: 2.95s	remaining: 14.6s
168:	learn: 0.6415722	total: 2.97s	remaining: 14.6s
169:	learn: 0.6415491	total: 2.99s	remaining: 14.6s
170:	learn: 0.6415235	total: 3.01s	remaining: 14.6s
171:	learn: 0.6414979	total: 3.02s	remaining: 14.6s
172:	learn: 0.6414792	total: 3.04s	remaining: 14.5s
173:	learn: 0.6414511	total: 3.06s	remaining: 14.5s
174:	learn: 0.6414293	total: 3.08s	remaining: 14.5s
175:	learn: 0.6414083	total: 3.09s	remaining: 14.5s
176:	learn: 0.6413866	total: 3.11s	remaining: 14.5s
177:	learn: 0.6413605	total: 3.13s	remaining: 14.4s
178:	learn: 0.6413424	total: 3.15s	remaining: 14.4s
179:	learn: 0.6413267	total: 3.16s	remaining: 14.4s
180:	learn: 0.6412986	total: 3.18s	remaining: 14.4s
181:	learn: 0.6412764	total: 3.2s	remaining: 14.4s
182:	learn: 0.6412553	total: 3.22s	remaining: 14.4s
183:	learn: 0.6412330	total: 3.23s	remaining: 14.3s
184:	learn: 0.6412075	total: 3.25s	remaining: 14.3s
185:	learn: 0

326:	learn: 0.6388893	total: 5.76s	remaining: 11.9s
327:	learn: 0.6388686	total: 5.78s	remaining: 11.8s
328:	learn: 0.6388578	total: 5.79s	remaining: 11.8s
329:	learn: 0.6388453	total: 5.81s	remaining: 11.8s
330:	learn: 0.6388317	total: 5.83s	remaining: 11.8s
331:	learn: 0.6388149	total: 5.84s	remaining: 11.8s
332:	learn: 0.6388025	total: 5.86s	remaining: 11.7s
333:	learn: 0.6387898	total: 5.88s	remaining: 11.7s
334:	learn: 0.6387805	total: 5.89s	remaining: 11.7s
335:	learn: 0.6387627	total: 5.91s	remaining: 11.7s
336:	learn: 0.6387481	total: 5.93s	remaining: 11.7s
337:	learn: 0.6387350	total: 5.96s	remaining: 11.7s
338:	learn: 0.6387206	total: 5.98s	remaining: 11.7s
339:	learn: 0.6387012	total: 6s	remaining: 11.6s
340:	learn: 0.6386889	total: 6.02s	remaining: 11.6s
341:	learn: 0.6386721	total: 6.04s	remaining: 11.6s
342:	learn: 0.6386612	total: 6.06s	remaining: 11.6s
343:	learn: 0.6386468	total: 6.08s	remaining: 11.6s
344:	learn: 0.6386348	total: 6.1s	remaining: 11.6s
345:	learn: 0.63

495:	learn: 0.6367163	total: 8.61s	remaining: 8.75s
496:	learn: 0.6367019	total: 8.63s	remaining: 8.73s
497:	learn: 0.6366911	total: 8.65s	remaining: 8.71s
498:	learn: 0.6366806	total: 8.66s	remaining: 8.7s
499:	learn: 0.6366714	total: 8.68s	remaining: 8.68s
500:	learn: 0.6366625	total: 8.69s	remaining: 8.66s
501:	learn: 0.6366497	total: 8.71s	remaining: 8.64s
502:	learn: 0.6366392	total: 8.73s	remaining: 8.62s
503:	learn: 0.6366287	total: 8.74s	remaining: 8.6s
504:	learn: 0.6366096	total: 8.76s	remaining: 8.59s
505:	learn: 0.6365982	total: 8.77s	remaining: 8.57s
506:	learn: 0.6365851	total: 8.79s	remaining: 8.55s
507:	learn: 0.6365694	total: 8.81s	remaining: 8.53s
508:	learn: 0.6365610	total: 8.82s	remaining: 8.51s
509:	learn: 0.6365503	total: 8.84s	remaining: 8.49s
510:	learn: 0.6365405	total: 8.86s	remaining: 8.48s
511:	learn: 0.6365213	total: 8.88s	remaining: 8.46s
512:	learn: 0.6365020	total: 8.89s	remaining: 8.44s
513:	learn: 0.6364876	total: 8.91s	remaining: 8.42s
514:	learn: 0.

663:	learn: 0.6347416	total: 11.4s	remaining: 5.79s
664:	learn: 0.6347272	total: 11.4s	remaining: 5.77s
665:	learn: 0.6347162	total: 11.5s	remaining: 5.75s
666:	learn: 0.6347100	total: 11.5s	remaining: 5.73s
667:	learn: 0.6347005	total: 11.5s	remaining: 5.71s
668:	learn: 0.6346866	total: 11.5s	remaining: 5.7s
669:	learn: 0.6346787	total: 11.5s	remaining: 5.68s
670:	learn: 0.6346682	total: 11.5s	remaining: 5.66s
671:	learn: 0.6346564	total: 11.6s	remaining: 5.64s
672:	learn: 0.6346448	total: 11.6s	remaining: 5.63s
673:	learn: 0.6346367	total: 11.6s	remaining: 5.61s
674:	learn: 0.6346248	total: 11.6s	remaining: 5.59s
675:	learn: 0.6346125	total: 11.6s	remaining: 5.57s
676:	learn: 0.6346038	total: 11.6s	remaining: 5.55s
677:	learn: 0.6345959	total: 11.7s	remaining: 5.54s
678:	learn: 0.6345775	total: 11.7s	remaining: 5.52s
679:	learn: 0.6345693	total: 11.7s	remaining: 5.5s
680:	learn: 0.6345566	total: 11.7s	remaining: 5.48s
681:	learn: 0.6345450	total: 11.7s	remaining: 5.46s
682:	learn: 0.

826:	learn: 0.6330018	total: 14.1s	remaining: 2.94s
827:	learn: 0.6329901	total: 14.1s	remaining: 2.92s
828:	learn: 0.6329769	total: 14.1s	remaining: 2.91s
829:	learn: 0.6329723	total: 14.1s	remaining: 2.89s
830:	learn: 0.6329640	total: 14.1s	remaining: 2.87s
831:	learn: 0.6329513	total: 14.1s	remaining: 2.86s
832:	learn: 0.6329408	total: 14.2s	remaining: 2.84s
833:	learn: 0.6329362	total: 14.2s	remaining: 2.82s
834:	learn: 0.6329291	total: 14.2s	remaining: 2.81s
835:	learn: 0.6329178	total: 14.2s	remaining: 2.79s
836:	learn: 0.6329052	total: 14.2s	remaining: 2.77s
837:	learn: 0.6328963	total: 14.3s	remaining: 2.75s
838:	learn: 0.6328852	total: 14.3s	remaining: 2.74s
839:	learn: 0.6328736	total: 14.3s	remaining: 2.72s
840:	learn: 0.6328654	total: 14.3s	remaining: 2.7s
841:	learn: 0.6328507	total: 14.3s	remaining: 2.69s
842:	learn: 0.6328362	total: 14.3s	remaining: 2.67s
843:	learn: 0.6328211	total: 14.3s	remaining: 2.65s
844:	learn: 0.6328141	total: 14.4s	remaining: 2.63s
845:	learn: 0

992:	learn: 0.6312540	total: 16.9s	remaining: 119ms
993:	learn: 0.6312473	total: 16.9s	remaining: 102ms
994:	learn: 0.6312346	total: 16.9s	remaining: 85.1ms
995:	learn: 0.6312213	total: 17s	remaining: 68.1ms
996:	learn: 0.6312119	total: 17s	remaining: 51.1ms
997:	learn: 0.6311955	total: 17s	remaining: 34.1ms
998:	learn: 0.6311846	total: 17s	remaining: 17ms
999:	learn: 0.6311729	total: 17s	remaining: 0us


In [78]:
regressors = [LinReg,
           Dtree,
           Rforest,
          xgb_pipe,
           svr_pipe,
          lgb_pipe,
          cb_pipe]

In [85]:
val_predictions = pd.DataFrame()
val_prediction = pd.Series
for reg in regressors:
    val_prediction = pd.Series(reg.predict(X_val))
    val_predictions[regressors.index(reg)] = val_prediction

mean_squared_error(Y_val, stacker_cb_model.predict(predictions), squared = False)

0.7189139537886304

In [63]:
X_train.head()

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
78850   0.707670  0.619905  0.334831  0.628941  0.832495  0.430448  0.412560   
36119   0.327272  0.356516  0.618076  0.303311  0.610909  0.537816  0.576739   
123670  0.467393  0.358361  0.501804  0.851466  0.802002  0.315503  0.377088   
12763   0.520106  0.168235  0.294885  0.275858  0.719473  0.613012  0.420170   
55192   0.948061  0.820781  0.223465  0.475990  0.497556  0.883607  0.638241   

           cont8     cont9    cont10    cont11    cont12    cont13    cont14  \
78850   0.801106  0.587422  0.680544  0.286556  0.502270  0.658485  0.856029   
36119   0.358436  0.365183  0.539615  0.490192  0.697461  0.368717  0.348209   
123670  0.376216  0.342714  0.438676  0.234322  0.322752  0.348985  0.218593   
12763   0.385265  0.597194  0.839359  0.500932  0.637387  0.714115  0.239618   
55192   0.803582  0.897365  0.806929  0.789698  0.833048  0.907615  0.731381   

               0  
78850   7.878507  
36119   7.803078  
123670  7.847268  
12763   8.017267  
55192   8.010507

In [94]:
X_train.drop(columns=[0], axis = 1, inplace=True)

In [95]:
X_train

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
78850   0.707670  0.619905  0.334831  0.628941  0.832495  0.430448  0.412560   
36119   0.327272  0.356516  0.618076  0.303311  0.610909  0.537816  0.576739   
123670  0.467393  0.358361  0.501804  0.851466  0.802002  0.315503  0.377088   
12763   0.520106  0.168235  0.294885  0.275858  0.719473  0.613012  0.420170   
55192   0.948061  0.820781  0.223465  0.475990  0.497556  0.883607  0.638241   
...          ...       ...       ...       ...       ...       ...       ...   
165959  0.669965  0.267008  0.247021  0.498890  0.282104  0.829169  0.752037   
186464  0.474306  0.359148  0.565569  0.315088  0.791018  0.623853  0.542710   
153709  0.721867  0.424421  0.594003  0.730605  0.281399  0.586627  0.811631   
239500  0.439958  0.089989  0.506192  0.797017  0.456215  0.368526  0.373182   
103904  0.245833  0.783075  0.550999  0.837185  0.629644  0.201868  0.295825   

           cont8     cont9    cont10  ...  cont10_cont11  cont10_cont12  \
78850   0.801106  0.587422  0.680544  ...       0.195014       0.341817   
36119   0.358436  0.365183  0.539615  ...       0.264515       0.376360   
123670  0.376216  0.342714  0.438676  ...       0.102791       0.141583   
12763   0.385265  0.597194  0.839359  ...       0.420462       0.534997   
55192   0.803582  0.897365  0.806929  ...       0.637230       0.672211   
...          ...       ...       ...  ...            ...            ...   
165959  0.871217  0.577007  0.819203  ...       0.670018       0.634439   
186464  0.639738  0.377893  0.583425  ...       0.419310       0.268536   
153709  0.908906  0.579120  0.602087  ...       0.447616       0.488435   
239500  0.537294  0.690091  0.412977  ...       0.183959       0.117354   
103904  0.615433  0.293539  0.355216  ...       0.109482       0.089235   

        cont10_cont13  cont10_cont14  cont11_cont12  cont11_cont13  \
78850        0.448128       0.582565       0.143928       0.188693   
36119        0.198965       0.187899       0.341889       0.180742   
123670       0.153091       0.095891       0.075628       0.081775   
12763        0.599399       0.201126       0.319287       0.357723   
55192        0.732381       0.590172       0.657856       0.716742   
...               ...            ...            ...            ...   
165959       0.718016       0.336801       0.633422       0.716864   
186464       0.287850       0.349379       0.330802       0.354594   
153709       0.477979       0.208268       0.603106       0.590195   
239500       0.244778       0.296749       0.126582       0.264024   
103904       0.119467       0.296948       0.077427       0.103659   

        cont11_cont14  cont12_cont13  cont12_cont14  cont13_cont14  
78850        0.245300       0.330737       0.429957       0.563682  
36119        0.170689       0.257165       0.242862       0.128390  
123670       0.051221       0.112635       0.070551       0.076285  
12763        0.120032       0.455168       0.152729       0.171115  
55192        0.577569       0.756087       0.609275       0.663812  
...               ...            ...            ...            ...  
165959       0.336260       0.678798       0.318405       0.360349  
186464       0.430389       0.227091       0.275632       0.295457  
153709       0.257164       0.644016       0.280615       0.274608  
239500       0.320081       0.168431       0.204192       0.425903  
103904       0.257655       0.084488       0.210005       0.281153  

[239999 rows x 105 columns]

In [97]:
regressors = [LinReg,
           Dtree,
           Rforest,
          xgb_pipe,
           svr_pipe,
          lgb_pipe,
          cb_pipe]

new_df = X_train
prediction = pd.Series
for reg in regressors:
    prediction = pd.Series(reg.predict(new_df))
    new_df[regressors.index(reg)] = prediction
        
new_df.head()

ValueError: X has 106 features, but ColumnTransformer is expecting 105 features as input.

In [98]:
X_train.head()

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
78850   0.707670  0.619905  0.334831  0.628941  0.832495  0.430448  0.412560   
36119   0.327272  0.356516  0.618076  0.303311  0.610909  0.537816  0.576739   
123670  0.467393  0.358361  0.501804  0.851466  0.802002  0.315503  0.377088   
12763   0.520106  0.168235  0.294885  0.275858  0.719473  0.613012  0.420170   
55192   0.948061  0.820781  0.223465  0.475990  0.497556  0.883607  0.638241   

           cont8     cont9    cont10  ...  cont10_cont12  cont10_cont13  \
78850   0.801106  0.587422  0.680544  ...       0.341817       0.448128   
36119   0.358436  0.365183  0.539615  ...       0.376360       0.198965   
123670  0.376216  0.342714  0.438676  ...       0.141583       0.153091   
12763   0.385265  0.597194  0.839359  ...       0.534997       0.599399   
55192   0.803582  0.897365  0.806929  ...       0.672211       0.732381   

        cont10_cont14  cont11_cont12  cont11_cont13  cont11_cont14  \
78850        0.582565       0.143928       0.188693       0.245300   
36119        0.187899       0.341889       0.180742       0.170689   
123670       0.095891       0.075628       0.081775       0.051221   
12763        0.201126       0.319287       0.357723       0.120032   
55192        0.590172       0.657856       0.716742       0.577569   

        cont12_cont13  cont12_cont14  cont13_cont14         0  
78850        0.330737       0.429957       0.563682  7.879019  
36119        0.257165       0.242862       0.128390  7.745668  
123670       0.112635       0.070551       0.076285  7.846966  
12763        0.455168       0.152729       0.171115  8.043750  
55192        0.756087       0.609275       0.663812  7.890516  

[5 rows x 106 columns]

In [99]:
new_df = pd.concat([X_train, predictions],axis = 1)
new_df.head()

cont1     cont2     cont3     cont4     cont5     cont6     cont7  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1  0.388053  0.621104  0.686102  0.501149  0.643790  0.449805  0.510824   
2  0.834950  0.227436  0.301584  0.293408  0.606839  0.829175  0.506143   
3  0.820708  0.160155  0.546887  0.726104  0.282444  0.785108  0.752758   
4  0.935278  0.421235  0.303801  0.880214  0.665610  0.830131  0.487113   

      cont8     cont9    cont10  ...  cont12_cont14  cont13_cont14         0  \
0       NaN       NaN       NaN  ...            NaN            NaN       NaN   
1  0.580748  0.418335  0.432632  ...       0.160715       0.136693  8.028024   
2  0.558771  0.587603  0.823312  ...       0.205377       0.267572  7.882075   
3  0.823267  0.574466  0.580843  ...       0.228693       0.255567  7.791011   
4  0.604157  0.874658  0.863427  ...       0.392397       0.407847  8.016371   

          0         1         2         3         4         5         6  
0  7.782168  7.933705  7.859719  8.021277  7.716206  8.118279  8.170052  
1  7.995529  7.933705  7.881026  7.850214  8.006899  7.830854  7.810715  
2  7.847625  7.802609  7.707600  7.690536  7.937106  7.710285  7.795841  
3  8.045513  7.933705  7.984601  8.071290  8.102855  8.061442  8.056379  
4  7.933525  7.933705  7.925735  8.022994  7.945834  7.985992  8.021769  

[5 rows x 113 columns]

In [83]:
new_df.describe()

cont1          cont2          cont3          cont4  \
count  239999.000000  239999.000000  239999.000000  239999.000000   
mean        0.506822       0.497849       0.521641       0.515710   
std         0.203969       0.228144       0.200776       0.232891   
min        -0.077238      -0.024398       0.026331       0.152761   
25%         0.342964       0.319856       0.344061       0.295107   
50%         0.483952       0.553152       0.551477       0.482997   
75%         0.643736       0.731349       0.648565       0.748543   
max         1.016227       0.859697       1.006955       1.010402   

               cont5          cont6          cont7          cont8  \
count  239999.000000  239999.000000  239999.000000  239999.000000   
mean        0.502030       0.526452       0.488184       0.525231   
std         0.220870       0.217886       0.181294       0.216247   
min         0.276377       0.083704      -0.026628       0.217725   
25%         0.284108       0.356009       0.346646       0.341615   
50%         0.451621       0.470957       0.466832       0.483310   
75%         0.670966       0.693509       0.581764       0.685572   
max         1.034046       1.043858       1.066167       1.024427   

               cont9         cont10  ...  cont12_cont14  cont13_cont14  \
count  239999.000000  239999.000000  ...  239999.000000  239999.000000   
mean        0.459759       0.520416  ...       0.256334       0.283609   
std         0.196566       0.201796  ...       0.160164       0.177450   
min        -0.240604      -0.085046  ...       0.023246       0.013342   
25%         0.330786       0.375425  ...       0.131727       0.137342   
50%         0.416945       0.458747  ...       0.217400       0.239493   
75%         0.574929       0.699343  ...       0.336313       0.383832   
max         1.004114       1.199951  ...       0.849631       0.824752   

                   0             0             1             2             3  \
count  191961.000000  60000.000000  60000.000000  60000.000000  60000.000000   
mean        7.907813      7.907212      7.907706      7.907590      7.907716   
std         0.135497      0.135146      0.086587      0.140800      0.200304   
min         7.058579      7.232281      7.802609      7.278262      6.766279   
25%         7.818247      7.818351      7.802609      7.815116      7.771212   
50%         7.899303      7.899562      7.933705      7.888008      7.896879   
75%         7.989870      7.989269      7.933705      7.979642      8.029575   
max         8.713970      8.913500      8.347718      9.011379      9.347747   

                  4             5             6  
count  60000.000000  60000.000000  60000.000000  
mean       7.939074      7.907213      7.907701  
std        0.195239      0.207318      0.214143  
min        6.959655      7.018181      7.083555  
25%        7.807897      7.766179      7.762634  
50%        7.933688      7.893953      7.895447  
75%        8.066545      8.033232      8.038148  
max        9.248959      9.344478      9.346866  

[8 rows x 113 columns]

In [84]:
Y_train.describe()

count    239999.000000
mean          7.907796
std           0.733052
min           4.256207
25%           7.331165
50%           7.943256
75%           8.471183
max          10.267569
Name: target, dtype: float64

In [100]:
stacker2_cb_model = cb.CatBoostRegressor()

stacker2_cb_model.fit(new_df, Y_train)

CatBoostError: Length of label=239999 and length of data=252045 is different.

In [57]:
lgb_params_grid ={'max_depth': [2,4,8,16,24,-1],
                 'num_leaves': [10,100, 1000],
                 'reg_alpha':[0, 0.1, 1]}

stack_lgb = lgb.LGBMRegressor(n_estimators = 200, n_jobs = -1)

stack_lgbregressor = GridSearchCV(stack_lgb, 
                    param_grid=lgb_params_grid, 
                    cv=5, 
                    return_train_score= True, 
                    scoring = 'neg_root_mean_squared_error',
                    n_jobs=-1)


stacked_tuned_lgb = stack_lgbregressor.fit(new_df, Y_train)

ValueError: Found input variables with inconsistent numbers of samples: [288037, 239999]

In [54]:
stack_predictions = pd.DataFrame()
prediction = pd.Series
for reg in regressors:
    prediction = pd.Series(reg.predict(X_val))
    stack_predictions[regressors.index(reg)] = prediction

mean_squared_error(Y_val, stack_lgbregressor.predict(stack_predictions), squared = False)

0.7103555992744138